# Load Libraries

In [1]:
import os

import pandas as pd
import numpy as np

import huggingface_hub
import datasets

import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.patches as mpatches

from datetime import datetime, timezone

import plotly
import plotly.express as px
import plotly.graph_objects as go

plotly.offline.init_notebook_mode(connected=True)

In [2]:
# Create the directory for plots
directory = "./plots"
if not os.path.exists(directory):
    os.makedirs(directory)

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
# Set colours
colors = ["#FF9D00", "#FFD21E", "#FF323D", "#32343D", "#297373", "#CD4631"]

ORANGE = "#FF9D00"
YELLOW = "#FFD21E"
RED = "#FF323D"
BLACK = "#32343D"
GREEN = "#297373"
DARK_ORANGE = "#CD4631"

# Data Loading and Preprocessing

## Load V1

In [5]:
# Load the v1 JSONL file
ds = datasets.load_dataset("open-llm-leaderboard/contents", split="train")
data_v1 = ds.to_pandas()
data_v1.shape

(7260, 26)

In [6]:
# Drop contaminated models
# There are two of them with specific names
data_v1 = data_v1[~data_v1.eval_name.str.contains("contaminated")]

In [7]:
data_v1.shape

(7258, 26)

In [8]:
data_v1.head()

eval_name Precision  \
0                    0-hero_Matter-0.1-7B_bfloat16  bfloat16   
1        0-hero_Matter-0.1-7B-DPO-preview_bfloat16  bfloat16   
2              0-hero_Matter-0.1-7B-boost_bfloat16  bfloat16   
3          0-hero_Matter-0.1-7B-boost-DPO_bfloat16  bfloat16   
4  0-hero_Matter-0.1-7B-boost-DPO-preview_bfloat16  bfloat16   

                                  Type  T Weight type        Architecture  \
0  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   
1  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   
2  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   
3  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   
4  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   

                                               Model  \
0  <a target="_blank" href="https://huggingface.c...   
1  <a target="_blank" href="https://huggingface.c...   
2  <a target="_blank" href="https://huggingface.c...   
3  <a target="_blank" href="https://huggingface.c...   
4  <a target="_blank" href="https://huggingface.c...   

                                 fullname  \
0                    0-hero/Matter-0.1-7B   
1        0-hero/Matter-0.1-7B-DPO-preview   
2              0-hero/Matter-0.1-7B-boost   
3          0-hero/Matter-0.1-7B-boost-DPO   
4  0-hero/Matter-0.1-7B-boost-DPO-preview   

                                  Model sha  Average ⬆️ Hub License  Hub ❤️  \
0  035c8193ce71be90be7d90098669afb9164ec6cb   63.391248  apache-2.0       0   
1  78040e4754051df49dd907cf1fd46a6b8a6cc30f   64.870290  apache-2.0       0   
2  ba56089eed1211f02e8d0ff47901e77b0cd48f83   63.223517  apache-2.0       0   
3  5bee9978fcf2188f1070b67f6d94be344fdd99c0   65.985858                   0   
4  d390fb35a781129efd26d53f7ecdb513c0c3da27   65.767435  apache-2.0       2   

   #Params (B)  Available on the hub  Merged   MoE  Flagged  \
0            7                  True    True  True     True   
1            7                  True    True  True     True   
2            7                  True    True  True     True   
3            7                 False    True  True     True   
4            7                  True    True  True     True   

                   date  Chat Template        ARC  HellaSwag       MMLU  \
0  2024-03-21T06:05:50Z          False  61.774744  82.135033  62.423731   
1  2024-03-23T04:13:58Z          False  62.713311  82.991436  62.700299   
2  2024-03-21T06:05:38Z          False  62.627986  81.507668  61.967618   
3  2024-03-22T15:02:21Z          False  65.017065  83.081060  61.873805   
4  2024-03-22T07:40:42Z          False  64.590444  82.871938  62.017625   

   TruthfulQA  Winogrande      GSM8K  Maintainers Choice  
0   42.439513   77.821626  53.752843               False  
1   45.790101   78.847672  56.178923               False  
2   54.702404   75.927388  42.608036               False  
3   60.293632   75.611681  50.037908               False  
4   58.859162   75.848461  50.416983               False

In [9]:
# Display V1 columns
columns_v1 = data_v1.columns
print(f"V1 columns: {columns_v1}")

V1 columns: Index(['eval_name', 'Precision', 'Type', 'T', 'Weight type', 'Architecture',
       'Model', 'fullname', 'Model sha', 'Average ⬆️', 'Hub License', 'Hub ❤️',
       '#Params (B)', 'Available on the hub', 'Merged', 'MoE', 'Flagged',
       'date', 'Chat Template', 'ARC', 'HellaSwag', 'MMLU', 'TruthfulQA',
       'Winogrande', 'GSM8K', 'Maintainers Choice'],
      dtype='object')


## Load V2

In [10]:
# Load the v2 JSONL file
ds = datasets.load_dataset("open-llm-leaderboard/contents_v2", split="train")
data_v2 = ds.to_pandas()
data_v2.shape

Generating train split:   0%|          | 0/203 [00:00<?, ? examples/s]

(203, 32)

In [11]:
data_v2.head()

eval_name Precision  \
0                   upstage_SOLAR-10.7B-v1.0_float16   float16   
1          upstage_SOLAR-10.7B-Instruct-v1.0_float16   float16   
2  togethercomputer_RedPajama-INCITE-Instruct-3B-...   float16   
3  togethercomputer_RedPajama-INCITE-Chat-3B-v1_f...   float16   
4  togethercomputer_RedPajama-INCITE-Base-3B-v1_f...   float16   

                                       Type  T Weight type  \
0                              🟢 pretrained  🟢    Original   
1       💬 chat models (RLHF, DPO, IFT, ...)  💬    Original   
2  🔶 fine-tuned on domain-specific datasets  🔶    Original   
3  🔶 fine-tuned on domain-specific datasets  🔶    Original   
4                              🟢 pretrained  🟢    Original   

         Architecture                                              Model  \
0    LlamaForCausalLM  <a target="_blank" href="https://huggingface.c...   
1    LlamaForCausalLM  <a target="_blank" href="https://huggingface.c...   
2  GPTNeoXForCausalLM  <a target="_blank" href="https://huggingface.c...   
3  GPTNeoXForCausalLM  <a target="_blank" href="https://huggingface.c...   
4  GPTNeoXForCausalLM  <a target="_blank" href="https://huggingface.c...   

                                           fullname  \
0                          upstage/SOLAR-10.7B-v1.0   
1                 upstage/SOLAR-10.7B-Instruct-v1.0   
2  togethercomputer/RedPajama-INCITE-Instruct-3B-v1   
3      togethercomputer/RedPajama-INCITE-Chat-3B-v1   
4      togethercomputer/RedPajama-INCITE-Base-3B-v1   

                                  Model sha  Average ⬆️   Hub License  Hub ❤️  \
0  a45090b8e56bdc2b8e32e46b3cd782fc0bea1fa5   17.072003    apache-2.0     248   
1  c08c25ed66414a878fe0401a3596d536c083606c   19.961989  cc-by-nc-4.0     592   
2  0c66778ee09a036886741707733620b91057909a    5.877290    apache-2.0      91   
3  f0e0995eba801096ed04cb87931d96a8316871af    4.950649    apache-2.0     147   
4  094fbdd0c911feb485ce55de1952ab2e75277e1e    5.645099    apache-2.0      90   

   #Params (B)  Available on the hub  Merged   MoE  Flagged  \
0           10                  True    True  True    False   
1           10                  True    True  True    False   
2            3                  True    True  True    False   
3            3                  True    True  True    False   
4            3                  True    True  True    False   

                   date  Chat Template  IFEval Raw     IFEval   BBH Raw  \
0  2024-06-12T12:27:42Z          False    0.242126  24.212645  0.509387   
1  2024-06-12T12:06:58Z           True    0.473661  47.366100  0.516249   
2  2024-06-12T12:07:46Z          False    0.212426  21.242636  0.314602   
3  2024-06-13T17:58:59Z          False    0.165215  16.521496  0.321669   
4  2024-06-12T12:28:23Z          False    0.229363  22.936254  0.306040   

         BBH  MATH Lvl 5 Raw  MATH Lvl 5  GPQA Raw      GPQA  MUSR Raw  \
0  29.789358        0.021148    2.114804  0.281040  4.138702  0.437156   
1  31.872402        0.000000    0.000000  0.308725  7.829978  0.389937   
2   4.510786        0.006042    0.604230  0.247483  0.000000  0.388604   
3   5.164728        0.003021    0.302115  0.244128  0.000000  0.368448   
4   3.518608        0.009063    0.906344  0.243289  0.000000  0.373875   

        MUSR  MMLU-PRO Raw   MMLU-PRO  Maintainer's Highlight  
0  13.677865      0.340010  26.667775                    True  
1   6.942188      0.313830  23.758865                    True  
2   6.408854      0.110954   1.217125                    True  
3   5.089323      0.112699   1.411052                    True  
4   4.001042      0.111120   1.235594                    True

In [12]:
# Display V2 columns
columns_v2 = data_v2.columns
print(f"V2 columns: {columns_v2}")

V2 columns: Index(['eval_name', 'Precision', 'Type', 'T', 'Weight type', 'Architecture',
       'Model', 'fullname', 'Model sha', 'Average ⬆️', 'Hub License', 'Hub ❤️',
       '#Params (B)', 'Available on the hub', 'Merged', 'MoE', 'Flagged',
       'date', 'Chat Template', 'IFEval Raw', 'IFEval', 'BBH Raw', 'BBH',
       'MATH Lvl 5 Raw', 'MATH Lvl 5', 'GPQA Raw', 'GPQA', 'MUSR Raw', 'MUSR',
       'MMLU-PRO Raw', 'MMLU-PRO', 'Maintainer's Highlight'],
      dtype='object')


## Define Tasks

In [13]:
tasks_v1 = ['ARC', 'HellaSwag', 'MMLU', 'TruthfulQA', 'Winogrande', 'GSM8K']
tasks_v2 = ['IFEval', 'BBH', 'MATH Lvl 5', 'GPQA', 'MUSR', 'MMLU-PRO']
tasks_v2_raw = ['IFEval Raw', 'BBH Raw', 'MATH Lvl 5 Raw', 'GPQA Raw', 'MUSR Raw', 'MMLU-PRO Raw']

## Add Models Creation Date

In [14]:
# version 1
for i, row in data_v1.iterrows():
    try:
        data_v1.at[i, 'date'] = huggingface_hub.model_info(row['fullname']).created_at
    except Exception:
        continue

Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.
Invalid model-index. Not loading eval results into CardData.


In [15]:
data_v1.head(2)

eval_name Precision  \
0              0-hero_Matter-0.1-7B_bfloat16  bfloat16   
1  0-hero_Matter-0.1-7B-DPO-preview_bfloat16  bfloat16   

                                  Type  T Weight type        Architecture  \
0  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   
1  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  MistralForCausalLM   

                                               Model  \
0  <a target="_blank" href="https://huggingface.c...   
1  <a target="_blank" href="https://huggingface.c...   

                           fullname                                 Model sha  \
0              0-hero/Matter-0.1-7B  035c8193ce71be90be7d90098669afb9164ec6cb   
1  0-hero/Matter-0.1-7B-DPO-preview  78040e4754051df49dd907cf1fd46a6b8a6cc30f   

   Average ⬆️ Hub License  Hub ❤️  #Params (B)  Available on the hub  Merged  \
0   63.391248  apache-2.0       0            7                  True    True   
1   64.870290  apache-2.0       0            7                  True    True   

    MoE  Flagged                       date  Chat Template        ARC  \
0  True     True  2024-03-20 05:57:38+00:00          False  61.774744   
1  True     True  2024-03-19 11:27:26+00:00          False  62.713311   

   HellaSwag       MMLU  TruthfulQA  Winogrande      GSM8K  Maintainers Choice  
0  82.135033  62.423731   42.439513   77.821626  53.752843               False  
1  82.991436  62.700299   45.790101   78.847672  56.178923               False

In [16]:
# version 2
for i, row in data_v2.iterrows():
    data_v2.at[i, 'date'] = huggingface_hub.model_info(row['fullname']).created_at

In [17]:
data_v2.head(2)

eval_name Precision  \
0           upstage_SOLAR-10.7B-v1.0_float16   float16   
1  upstage_SOLAR-10.7B-Instruct-v1.0_float16   float16   

                                  Type  T Weight type      Architecture  \
0                         🟢 pretrained  🟢    Original  LlamaForCausalLM   
1  💬 chat models (RLHF, DPO, IFT, ...)  💬    Original  LlamaForCausalLM   

                                               Model  \
0  <a target="_blank" href="https://huggingface.c...   
1  <a target="_blank" href="https://huggingface.c...   

                            fullname  \
0           upstage/SOLAR-10.7B-v1.0   
1  upstage/SOLAR-10.7B-Instruct-v1.0   

                                  Model sha  Average ⬆️   Hub License  Hub ❤️  \
0  a45090b8e56bdc2b8e32e46b3cd782fc0bea1fa5   17.072003    apache-2.0     248   
1  c08c25ed66414a878fe0401a3596d536c083606c   19.961989  cc-by-nc-4.0     592   

   #Params (B)  Available on the hub  Merged   MoE  Flagged  \
0           10                  True    True  True    False   
1           10                  True    True  True    False   

                        date  Chat Template  IFEval Raw     IFEval   BBH Raw  \
0  2023-12-12 14:57:41+00:00          False    0.242126  24.212645  0.509387   
1  2023-12-12 12:39:22+00:00           True    0.473661  47.366100  0.516249   

         BBH  MATH Lvl 5 Raw  MATH Lvl 5  GPQA Raw      GPQA  MUSR Raw  \
0  29.789358        0.021148    2.114804  0.281040  4.138702  0.437156   
1  31.872402        0.000000    0.000000  0.308725  7.829978  0.389937   

        MUSR  MMLU-PRO Raw   MMLU-PRO  Maintainer's Highlight  
0  13.677865       0.34001  26.667775                    True  
1   6.942188       0.31383  23.758865                    True

# MMLU vs MMLU-Pro V1

In [18]:
mmlu_pro = 'MMLU-PRO'
math = 'MATH Lvl 5'
gpqa = "GPQA"

# Extracting the relevant information
v1_data = data_v1[['fullname', 'MMLU', 'GSM8K']]
v2_data = data_v2[['fullname', mmlu_pro, math, gpqa]]

# Merging the two dataframes on 'eval_name'
merged_data = pd.merge(v1_data, v2_data, on='fullname', how='inner')

In [19]:
merged_data.head()

fullname       MMLU      GSM8K   MMLU-PRO  MATH Lvl 5  \
0       01-ai/Yi-1.5-34B  77.995719  73.237301  40.732122   14.048338   
1   01-ai/Yi-1.5-34B-32K  78.153032   0.000000  41.212323   13.444109   
2  01-ai/Yi-1.5-34B-Chat  77.082840  71.645186  39.116061   23.338369   
3        01-ai/Yi-1.5-6B  64.726895  50.341168  23.343307    5.664653   
4        01-ai/Yi-1.5-6B  65.002720  49.810462  23.343307    5.664653   

        GPQA  
0  15.436242  
1  15.100671  
2  15.324385  
3   8.277405  
4   8.277405

- MMLU and MMLU_Pro are well correlated - overall, a model with High MMLU has a high MMLU Pro score
- For MATH vs GSM8K, we identify 3 groups:
    - "High" MATH score, very low v1 score (2 outliers): possible overfitting on MATH, or , more likely, one of these models with issues with eos tokens on GSM8K
    - Correlation between v2 and v1 score (most models)
    - Low MATH score, high GSM8K score: likely overfitting on GSM8K

In [22]:
# Mapping of comparisons to plot
mapping = [("MMLU", "MMLU-PRO", colors[1]), ("MMLU", "GPQA", colors[0])]

# Create a new figure object
fig = go.Figure()

# Add scatter plots for each mapping
for old, new, color in mapping:
    fig.add_trace(go.Scatter(
        x=merged_data[old],
        y=merged_data[new],
        mode='markers',
        marker_color=color,
        name=f'{new}=f({old})'
    ))

# Update layout
fig.update_layout(
    title='New scores as functions of old evaluations',
    xaxis=dict(title='v1 scores', range=[0, 100]),
    yaxis=dict(title='v2 scores', range=[-5, 80]),
    legend_title="Evaluations",
    showlegend=True,
    width=600,
    height=350,
)

with open("./plots/new_scores_vs_old.html", "w") as f:
    f.write(fig.to_html(full_html=False))

# Display the plot
fig.show()

In [40]:
# Custom color mapping
color_map = {'green': GREEN, 'red': RED, 'default': ORANGE}

# Add a new column for color based on more detailed conditions
conditions = [
    (merged_data['MATH Lvl 5'] > 0) & (merged_data['GSM8K'] > 0),
    (merged_data['MATH Lvl 5'] == 0) & (merged_data['GSM8K'] > 40),
    (merged_data['MATH Lvl 5'] > 0) & (merged_data['GSM8K'] == 0)
]

# Labels for each condition
labels = ['default', 'red', 'green']

# Use np.select to apply multiple conditions
merged_data['color'] = np.select(conditions, labels, default='default')

# Create the scatter plot using the new 'color' column for color-coding
fig = px.scatter(
    merged_data, 
    x='GSM8K', 
    y='MATH Lvl 5',
    labels={
        'GSM8K': 'GSM8K (v1)', 
        'MATH Lvl 5': 'MATH (v2)'
    },
    title='MATH (v2) as Function of GSM8K (v1)',
    color='color',
    color_discrete_map=color_map
)

# Update axes and layout
fig.update_xaxes(title_text='GSM8K (v1)')
fig.update_yaxes(title_text='MATH (v2)')
fig.update_layout(
    showlegend=False,
    width=600,
    height=350
)

with open("math_vs_gsm8k.html", "w") as f:
    f.write(fig.to_html(full_html=False))

fig.show()

- MMLU and MMLU_Pro are well correlated - overall, a model with High MMLU has a high MMLU Pro score
- For MATH vs GSM8K, we identify 3 groups:
    - "High" MATH score, very low v1 score (2 outliers): possible overfitting on MATH, or , more likely, one of these models with issues with eos tokens on GSM8K
    - Correlation between v2 and v1 score (most models)
    - Low MATH score, high GSM8K score: likely overfitting on GSM8K 

# Ranking Analysis between V1 and V2

In [41]:
# Extracting the relevant information for ranking comparison between v1 and v2
# We actually want to merge with correct precision if possible, else merge on what's available
v2_rank_data = data_v2[["fullname", "Average ⬆️"]]
v1_rank_data = data_v1[["fullname", "Average ⬆️"]]

In [42]:
# Renaming columns for clarity
v2_rank_data = v2_rank_data.rename(columns={"Average ⬆️": "v2_score"})
v1_rank_data = v1_rank_data.rename(columns={"Average ⬆️": "v1_score"})

In [43]:
# Merging the two dataframes on 'eval_name'
merged_rank_data = pd.merge(v1_rank_data, v2_rank_data, on="fullname", how="inner")

In [44]:
merged_rank_data = merged_rank_data.drop_duplicates(subset=["fullname"]).dropna()

In [45]:
merged_rank_data.head()

fullname   v1_score   v2_score
0       01-ai/Yi-1.5-34B  73.504618  25.812197
1   01-ai/Yi-1.5-34B-32K  60.700977  26.787600
2  01-ai/Yi-1.5-34B-Chat  74.823763  33.076818
3        01-ai/Yi-1.5-6B  61.566520  16.778059
5   01-ai/Yi-1.5-6B-Chat  66.167303  22.405532

In [46]:
# Calculating rank for v1 and v2 based on scores
merged_rank_data["v1_rank"] = merged_rank_data["v1_score"].rank(ascending=False)
merged_rank_data["v2_rank"] = merged_rank_data["v2_score"].rank(ascending=False)

In [47]:
# Calculating rank change and sort
merged_rank_data["rank_change"] = (
    merged_rank_data["v2_rank"] - merged_rank_data["v1_rank"]
)

merged_rank_data = merged_rank_data.sort_values("rank_change")
merged_rank_data = merged_rank_data.dropna()

In [48]:
merged_rank_data.sort_values(by="v1_rank", ascending = True).head(10)

fullname   v1_score   v2_score  v1_rank  \
89                abacusai/Smaug-72B-v0.1  80.481415  29.976022      1.0   
138  meta-llama/Meta-Llama-3-70B-Instruct  77.882051  36.670225      2.0   
88                abacusai/Smaug-34B-v0.1  77.285644  24.127214      3.0   
164              mlabonne/AlphaMonarch-7B  75.988300  17.913614      4.0   
165             mlabonne/Beyonder-4x7B-v3  75.654718  19.642237      5.0   
70                      Qwen/Qwen1.5-110B  75.415188  29.975375      6.0   
2                   01-ai/Yi-1.5-34B-Chat  74.823763  33.076818      7.0   
22        CohereForAI/c4ai-command-r-plus  74.618473  31.295336      8.0   
158          mistralai/Mixtral-8x22B-v0.1  74.471418  25.871531      9.0   
207     upstage/SOLAR-10.7B-Instruct-v1.0  74.200698  19.961989     10.0   

     v2_rank  rank_change  
89       5.0          4.0  
138      1.0         -1.0  
88      22.0         19.0  
164     59.0         55.0  
165     47.0         42.0  
70       6.0          0.0  
2        3.0         -4.0  
22       4.0         -4.0  
158     14.0          5.0  
207     45.0         35.0

In [49]:
merged_rank_data.sort_values(by="v2_rank", ascending = True).head(10)

fullname   v1_score   v2_score  \
138         meta-llama/Meta-Llama-3-70B-Instruct  77.882051  36.670225   
146           microsoft/Phi-3-medium-4k-instruct  73.448553  33.116864   
2                          01-ai/Yi-1.5-34B-Chat  74.823763  33.076818   
22               CohereForAI/c4ai-command-r-plus  74.618473  31.295336   
89                       abacusai/Smaug-72B-v0.1  80.481415  29.976022   
70                             Qwen/Qwen1.5-110B  75.415188  29.975375   
71                        Qwen/Qwen1.5-110B-Chat  68.006415  29.639560   
8                           01-ai/Yi-1.5-9B-Chat  69.555695  28.111418   
56   NousResearch/Nous-Hermes-2-Mixtral-8x7B-DPO  73.122196  27.343441   
1                           01-ai/Yi-1.5-34B-32K  60.700977  26.787600   

     v1_rank  v2_rank  rank_change  
138      2.0      1.0         -1.0  
146     13.0      2.0        -11.0  
2        7.0      3.0         -4.0  
22       8.0      4.0         -4.0  
89       1.0      5.0          4.0  
70       6.0      6.0          0.0  
71      34.0      7.0        -27.0  
8       21.0      8.0        -13.0  
56      14.0      9.0         -5.0  
1       71.0     10.0        -61.0

In [50]:
# Sorting merged_rank_data by 'rank_change'
merged_rank_data = merged_rank_data.sort_values('rank_change')

# Create a new column for color based on 'rank_change'
merged_rank_data['color'] = merged_rank_data['rank_change'].apply(lambda x: '#FF9D00' if x > 0 else '#32343D')

# Calculate the top 10 positive and negative rank changes
top_pos = merged_rank_data.nlargest(10, 'rank_change')
top_neg = merged_rank_data.nsmallest(10, 'rank_change')

# Combine the two dataframes
top_changes = pd.concat([top_pos, top_neg]).sort_values('rank_change')

# Create a column for detailed rank change information
top_changes["rank_change_info"] = top_changes.apply(
    lambda x: f"{int(x['v1_rank'])} → {int(x['v2_rank'])}", axis=1
)

top_changes.head()

fullname   v1_score   v2_score  v1_rank  v2_rank  \
1         01-ai/Yi-1.5-34B-32K  60.700977  26.787600     71.0     10.0   
7          01-ai/Yi-1.5-9B-32K  55.217184  19.937832     96.0     46.0   
42   Intel/neural-chat-7b-v3-1  59.900319  21.348573     76.0     40.0   
123                       gpt2  28.530425   6.754202    165.5    131.0   
12           01-ai/Yi-34B-Chat  63.173386  24.268419     55.0     21.0   

     rank_change    color rank_change_info  
1          -61.0  #32343D          71 → 10  
7          -50.0  #32343D          96 → 46  
42         -36.0  #32343D          76 → 40  
123        -34.5  #32343D        165 → 131  
12         -34.0  #32343D          55 → 21

In [59]:
# Invert the order to show declines first
top_changes_sorted = top_changes.sort_values("rank_change", ascending=False)

# Using Plotly Express to create a horizontal bar chart
fig = px.bar(
    top_changes_sorted,
    y="fullname",
    x="rank_change",
    text="rank_change_info",
    orientation='h',
    title="Top and Bottom Changes in Rankings from v1 to v2",
    height=700,
    width=800,
    template='plotly',
    color='rank_change',
    color_continuous_scale=[BLACK, ORANGE]
)

# Additional layout settings
fig.update_layout(
    xaxis_tickfont_size=14,
    yaxis=dict(title='Model'),
    bargap=0.1,  # gap between bars of adjacent location coordinates
    xaxis_range=[-85, 85],
    paper_bgcolor="rgba(0,0,0,0)",
    plot_bgcolor="rgba(0,0,0,0)",
    width=650,
    height=400
)

fig.update_yaxes(autorange="reversed")  # Reverse the y-axis order
fig.update_traces(textposition='outside')  # Set text labels to be outside the bars

# Save the figure as HTML
fig.write_html("./plots/rankings_change.html", full_html=False)

# Display the figure
fig.show()

# Params and Performance

In [52]:
# Set date
threshold_1 = datetime(2023, 10, 1, tzinfo=timezone.utc)
threshold_2 = datetime(2023, 12, 1, tzinfo=timezone.utc)
threshold_3 = datetime(2024, 2, 1, tzinfo=timezone.utc)
threshold_4 = datetime(2024, 5, 1, tzinfo=timezone.utc)

# Checking if thresholds are in the correct order
thresholds = [threshold_1, threshold_2, threshold_3, threshold_4]
print("Thresholds in correct order:", all(x < y for x, y in zip(thresholds, thresholds[1:])))

Thresholds in correct order: True


In [53]:
# Convert date columns to datetime if not already
data_v1['date'] = pd.to_datetime(data_v1['date'], utc=True)
data_v2['date'] = pd.to_datetime(data_v2['date'], utc=True)

In [54]:
# Calculate the mean performance score across the tasks for both versions
data_v1['mean_score_v1'] = data_v1[tasks_v1].mean(axis=1)
data_v2['mean_score_v2'] = data_v2[tasks_v2].mean(axis=1)

# Extract the necessary columns for plotting
full=False
if full:
    v1_data = data_v1[['fullname', '#Params (B)', 'mean_score_v1', 'date']]
    v2_data = data_v2[['fullname', '#Params (B)', 'mean_score_v2', 'date']]

    # Merge the data on fullname
    merged_data = pd.merge(v1_data, v2_data, on=['fullname', 'date', "#Params (B)"], how='outer')
else:
    v1_data = data_v1[['fullname', '#Params (B)', 'mean_score_v1']]
    v2_data = data_v2[['fullname', '#Params (B)', 'mean_score_v2', 'date']]

    # Merge the data on fullname
    merged_data = pd.merge(v1_data, v2_data, on=['fullname', "#Params (B)"], how='outer')

In [55]:
merged_data.dropna(subset="date", inplace=True)

merged_data["date"] = pd.to_datetime(merged_data["date"])
for row in merged_data["date"]:
    if not isinstance(row, pd._libs.tslibs.timestamps.Timestamp) or not isinstance(row, datetime):
        print(row, type(row))

In [58]:
# Create a new figure
fig = go.Figure()

# Add traces for each version and period
fig.add_trace(go.Scatter(
    x=merged_data['#Params (B)'][merged_data['date'] < threshold_1],
    y=merged_data['mean_score_v1'][merged_data['date'] < threshold_1],
    mode='markers',
    name='V1 - before Oct 2023',
    marker=dict(color=DARK_ORANGE)
))
fig.add_trace(go.Scatter(
    x=merged_data['#Params (B)'][(threshold_1 <= merged_data['date']) & (merged_data['date'] < threshold_2)],
    y=merged_data['mean_score_v1'][(threshold_1 <= merged_data['date']) & (merged_data['date'] < threshold_2)],
    mode='markers',
    name='V1 - Oct 2023 to Dec 2023',
    marker=dict(color=ORANGE)
))
fig.add_trace(go.Scatter(
    x=merged_data['#Params (B)'][merged_data['date'] >= threshold_2],
    y=merged_data['mean_score_v1'][merged_data['date'] >= threshold_2],
    mode='markers',
    name='V1 - Dec 2023 and after',
    marker=dict(color=YELLOW)
))

# Version 2: All data points
fig.add_trace(go.Scatter(
    x=merged_data['#Params (B)'],
    y=merged_data['mean_score_v2'],
    mode='markers',
    name='V2',
    marker=dict(color=BLACK)
))

# Update axes and layout
fig.update_layout(
    title="Model Complexity vs Performance",
    xaxis_title="Model Complexity (#Params in B)",
    yaxis_title="Mean Performance Score",
    legend_title="Version and Period",
    yaxis=dict(range=[-10, 100]),
    xaxis=dict(range=[-10, 150]),
    width=600,
    height=350
)

with open("./plots/model_size_vs_perf.html", "w") as f:
    f.write(fig.to_html(full_html=False))

# Show the figure
fig.show()